# Guided Project : Data Management with Databricks: Big Data with <img src="https://docs.delta.io/latest/_static/delta-lake-logo.png" width=300/>

<img src="https://upload.wikimedia.org/wikipedia/commons/9/97/Coursera-Logo_600x600.svg" width=50 height=50/>

**Project Scneario**: You are a Data Engineer working for an online clothing brand that sells a wide range of fashion Brands. The company's Supply Chain team has been tasked with building a dashboard to Analyze Orders history.

The supply chain team has been tasked with building a dashboard to **Analyze Orders history**. Your dashboard will be used to inform purchasing behaviour and ensure that the company has enough inventory to meet demand for the upcoming holiday season.

Throughout this real-world business scenario, you will learn how to create and ingest data into a delta table. Then use Databricks notebooks (using Python and SQL) to process/transform the data and produce the Supply chain dashboard. At the end you'll leverage Delta Lake's built-in functionalities such as merge operations and time travel to create a scalable data pipeline.

# TASK 2 - Upload project JSON files to Databricks file system

In [0]:
# First Check that the parameter "DBFS File Browser" is Enable. Navigate to "Settings > Admin > Workspace settings"  to check

### a. Upload ORDERS Json files in Databricks File System

In [0]:
## Load Data Using the UI to this path dbfs:/FileStore/SupplyChain/ORDERS_RAW/

### b. Check loaded files

In [0]:
# Use Databricks Utilities (dbutils). Documentation : https://docs.databricks.com/dev-tools/databricks-utils.html#ls-command-dbutilsfsls 
dbutils.fs.ls("dbfs:/FileStore/SupplyChain/ORDERS_RAW/")


Out[74]: [FileInfo(path='dbfs:/FileStore/SupplyChain/ORDERS_RAW/ORDERS_RAW_PART_001.json', name='ORDERS_RAW_PART_001.json', size=260483, modificationTime=1704134932000),
 FileInfo(path='dbfs:/FileStore/SupplyChain/ORDERS_RAW/ORDERS_RAW_PART_002.json', name='ORDERS_RAW_PART_002.json', size=260437, modificationTime=1704134932000),
 FileInfo(path='dbfs:/FileStore/SupplyChain/ORDERS_RAW/ORDERS_RAW_PART_003.json', name='ORDERS_RAW_PART_003.json', size=260640, modificationTime=1704134933000),
 FileInfo(path='dbfs:/FileStore/SupplyChain/ORDERS_RAW/ORDERS_RAW_PART_004.json', name='ORDERS_RAW_PART_004.json', size=4928, modificationTime=1704134933000),
 FileInfo(path='dbfs:/FileStore/SupplyChain/ORDERS_RAW/UPDATE_ORDERS_RAW.json', name='UPDATE_ORDERS_RAW.json', size=2628, modificationTime=1704387757000)]

# TASK 3 - Create Delta Table : ORDERS_RAW

### a. Read multiline json files using spark dataframe:

In [0]:
# Read multiple line json files using spark dataframeAPI


orders_raw_df = spark.read.option("multiline", "true").json("dbfs:/FileStore/SupplyChain/ORDERS_RAW/ORDERS_RAW_PART_*.json")

## Show the datafarme
orders_raw_df.show(n=5, truncate=False) 

## click on orders_raw_df to Check the schema

+---------------+-------------------+-----+-----------+-------------+----------+--------+------------+-----------------+-----------------------+--------+---------------+--------+------------+----------+
|BRAND          |CATEGORY           |COLOR|CUSTOMER_ID|ORDER_COUNTRY|ORDER_DATE|ORDER_ID|ORDER_STATUS|PAYMENT_METHOD   |PRODUCT_NAME           |QUANTITY|SHIPPING_METHOD|SIZE    |SUB-CATEGORY|UNIT_PRICE|
+---------------+-------------------+-----+-----------+-------------+----------+--------+------------+-----------------+-----------------------+--------+---------------+--------+------------+----------+
|Gap            |Men's Clothing     |Navy |2348       |Germany      |2023-01-11|ORD-200 |Shipped     |Cash on Delivery |Classic Cotton T-Shirt |6       |Express        |Size L  |Tops        |24.99     |
|Adidas Kids    |Kids Clothing      |Green|2149       |Mexico       |2023-01-11|ORD-1418|Delivered   |Credit/Debit Card|Green Hooded Sweatshirt|3       |Standard       |Size 14 |Tops      

In [0]:
#Validate loaded files Count Number of Rows in the DataFrame, the total Should be "1510"
orders_raw_df.count()

Out[76]: 1510

### ![b.](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) b. Create Delta Table ORDERS_RAW

Delta Lake is 100% compatible with Apache Spark&trade;, which makes it easy to get started with if you already use Spark for your big data workflows.
Delta Lake features APIs for **SQL**, **Python**, and **Scala**, so that you can use it in whatever language you feel most comfortable in.


   <img src="https://databricks.com/wp-content/uploads/2020/12/simplysaydelta.png" width=400/>

In [0]:
# First, Create Database SupplyChainDB if it doesn't exist
db = "SupplyChainDB"

spark.sql(f"CREATE DATABASE IF NOT EXISTS {db}")
spark.sql(f"USE {db}")

Out[77]: DataFrame[]

In [0]:
## Create DelaTable ORDERS_RAW in the metastore using DataFrame's schema and write data to it
## Documentation : https://docs.delta.io/latest/quick-start.html#create-a-table

orders_raw_df.write.mode("overwrite").format("delta").option("overwriteSchema", "True").saveAsTable("ORDERS_RAW")

### c. Show Created Delta Table:

In [0]:
%sql
-- Switch to SQL Cell using %SQL
SHOW tables
 
 -- Alternativerly you can use Python: display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

In [0]:
# Alternativerly you can use Python: display(spark.sql(f"SHOW TABLES"))
display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

**d. Validate data loaded successfully to Delta Table ORDERS_RAW**:

In [0]:
%sql
SELECT COUNT(*) FROM ORDERS_RAW


count(1) 1510

In [0]:
%sql
select * from ORDERS_RAW limit 5

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE Tumi Men's Accessories Black 2210 South Africa 2022-08-26 ORD-377 Cancelled PayPal Black Leather Backpack 10 Standard One Size Backpacks 399.99 Zara Kids Kids Clothing Pink 2005 Norway 2022-08-26 ORD-1137 Delivered Credit/Debit Card Pink Ruffled Skirt 2 Standard Size 6 Skirts 29.99 Adidas Kids Kids Clothing Blue 2112 Switzerland 2022-08-26 ORD-1279 Processing Credit/Debit Card Blue Denim Shorts 1 Standard Size 4T Shorts 19.99 Zara Men's Clothing Brown 2435 Netherlands 2022-08-26 ORD-554 Shipped Credit/Debit Card Men's Leather Moto Jacket 4 Standard Size XL Jackets 599.99 Ralph Lauren Men's Accessories Black 2112 Netherlands 2022-08-26 ORD-364 Processing PayPal Leather Briefcase 3 Standard One Size Briefcases 399.99

Databricks data profile. Run in Databricks to view.

**e. Decsribe Detail of the Delta Table**:

In [0]:
%sql

describe DETAIL ORDERS_RAW

-- Returns the basic metadata information of a delta table.

format id name description location createdAt lastModified partitionColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion tableFeatures statistics delta 23830470-b360-4716-a305-52e44d1767d4 spark_catalog.supplychaindb.orders_raw null dbfs:/user/hive/warehouse/supplychaindb.db/orders_raw 2024-01-02T09:18:04.454+0000 2024-01-05T16:16:22.000+0000 List() 4 57492 Map() 1 2 List(appendOnly, invariants) Map()

#Practice Activity 1 : Create INVENTORY Delta table

### a. Upload INVENTORY.Json file in DBFS

In [0]:
## Load the file using the UI to this path dbfs:/FileStore/SupplyChain/INVENTORY/

###b. Read the File using spark dataframe

In [0]:
inventory_df = spark.read.option("multiline","true").json("dbfs:/FileStore/SupplyChain/INVENTORY/INVENTORY.json")

## Show the datafarme
inventory_df.show(n=5, truncate=False)

+-------+----------+--------------------------+----------+-----+
|BRAND  |COLOR     |PRODUCT_NAME              |SIZE      |STOCK|
+-------+----------+--------------------------+----------+-----+
|J.Crew |Green     |Green Cargo Pants         |Size 32x32|58   |
|Theory |Grey      |Grey Turtleneck Sweater   |Size S    |42   |
|Ray-Ban|Gold/Brown|Classic Aviator Sunglasses|One Size  |53   |
|ASOS   |Black     |Men's Faux Leather Jacket |Size M    |40   |
|Levi's |Light Blue|Distressed Denim Shorts   |Size M    |46   |
+-------+----------+--------------------------+----------+-----+
only showing top 5 rows



### ![c.](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) c. Create Delta Table INVENTORY

In [0]:
# First, Create Database SupplyChainDB
db = "SupplyChainDB"
spark.sql(f"USE {db}")

Out[87]: DataFrame[]

In [0]:
## Create INVENTORY Delta Table 
inventory_df.write.mode("overwrite").format("delta").option("overwriteSchema", "True").saveAsTable("INVENTORY")

### d. Show Created Delta Tables:

In [0]:
%sql
-- Switch to SQL Cell using %sql
SHOW TABLES

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

In [0]:
# Alternativerly you can use Python: display(spark.sql(f"SHOW TABLES"))
display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

In [0]:
%sql
select * from INVENTORY limit 10

BRAND COLOR PRODUCT_NAME SIZE STOCK J.Crew Green Green Cargo Pants Size 32x32 58 Theory Grey Grey Turtleneck Sweater Size S 42 Ray-Ban Gold/Brown Classic Aviator Sunglasses One Size 53 ASOS Black Men's Faux Leather Jacket Size M 40 Levi's Light Blue Distressed Denim Shorts Size M 46 Gap Navy Classic Cotton T-Shirt Size L 44 Coach Black Leather Crossbody Bag One Size 53 Nike Kids Gray Gray Joggers Size 12 50 Steve Madden Black Lace-Up Combat Boots Size 8 65 Dr. Martens Black Black Leather Chelsea Boots Size 10 61

Databricks data profile. Run in Databricks to view.

# TASK 4 - Transform data in delta table

<a href="https://www.databricks.com/glossary/medallion-architecture" target="_blank">Medallion Architecture</a>   
</br>
<img src="https://databricks.com/wp-content/uploads/2020/09/delta-lake-medallion-model-scaled.jpg" width=900/>

During this Task you will : 
* 1- Read delta Table using Spark Dataframe
* 2- Convert Data Type String --> Date
* 3- Drop Rows with Null Values
* 4- Add a Computed Column "TOTAL_ORDER"
* 5- Create new deltatable Orders_Gold

### a. Read ORDERS_RAW delta table using spark Dataframe

In [0]:
#read Delta Table using spark dataframe

ORDERS_Gold_df=spark.read.table("supplychaindb.ORDERS_raw")

ORDERS_Gold_df.show(n=5,truncate=False)
# Click on ORDERS_DF to See the Schema of the Table. 

+------------+----------------+--------------+-----------+-------------+----------+--------+------------+-----------------+---------------------+--------+---------------+-------+------------+----------+
|BRAND       |CATEGORY        |COLOR         |CUSTOMER_ID|ORDER_COUNTRY|ORDER_DATE|ORDER_ID|ORDER_STATUS|PAYMENT_METHOD   |PRODUCT_NAME         |QUANTITY|SHIPPING_METHOD|SIZE   |SUB-CATEGORY|UNIT_PRICE|
+------------+----------------+--------------+-----------+-------------+----------+--------+------------+-----------------+---------------------+--------+---------------+-------+------------+----------+
|H&M Kids    |Kids Clothing   |Pink and Green|2066       |Hong Kong    |2022-01-21|ORD-1281|Processing  |Credit/Debit Card|Pink Floral Dress    |3       |Standard       |Size 6 |Dresses     |24.99     |
|H&M         |Women's Clothing|Cream         |2254       |Spain        |2022-01-23|ORD-541 |Delivered   |Credit/Debit Card|Women's Faux Fur Coat|4       |Standard       |Size M |Outerwear 

### b. Update ORDER_DATE Column's Data Type

In [0]:
#Use withColumn method & to_date()
# withColumn Documentation : https://spark.apache.org/docs/3.1.3/api/python/reference/api/pyspark.sql.DataFrame.withColumn.html
# TO_DATE() Documentation : https://docs.databricks.com/sql/language-manual/functions/to_date.html

from pyspark.sql.functions import *

ORDERS_Gold_df =  ORDERS_Gold_df.withColumn("ORDER_DATE", to_date(col("ORDER_DATE"), "yyyy-MM-dd"))

### c. Drop Rows with Null Values

In [0]:
# Count Nulls for each column
from pyspark.sql.functions import *

display(ORDERS_Gold_df.select([count(when(col(c).isNull(),c)).alias(c) for c in ORDERS_Gold_df.columns]))

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE 0 0 0 10 10 0 10 0 0 10 10 0 0 0 0

In [0]:
#  Remove Nulls using dropna() method which removes all rows with Null Values 

ORDERS_Gold_df = ORDERS_Gold_df.dropna()

ORDERS_Gold_df.count()

Out[96]: 1500

### d. Add new Column TOTAL_ORDER

In [0]:
#Use withColumn function
#Documentation : https://spark.apache.org/docs/3.1.3/api/python/reference/api/pyspark.sql.DataFrame.withColumn.html


ORDERS_Gold_df = ORDERS_Gold_df.withColumn("TOTAL_ORDER", col("QUANTITY")*col("UNIT_PRICE"))

# Display ORDERS_Gold_df to validate the creation of the New Column TOTAL_ORDER
display(ORDERS_Gold_df)

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE TOTAL_ORDER H&M Women's Clothing Cream 2254 Spain 2022-01-23 ORD-541 Delivered Credit/Debit Card Women's Faux Fur Coat 4 Standard Size M Outerwear 129.99 519.96 Canada Goose Men's Clothing Dark Green 2033 Hong Kong 2022-01-23 ORD-1388 Shipped Credit/Debit Card Men's Parka 2 Standard Size XL Jackets 999.99 1999.98 Zara Kids Kids Clothing Grey 2144 Switzerland 2022-01-24 ORD-1158 Delivered Credit/Debit Card Grey Hoodie 1 Standard Size L Sweatshirts 39.99 39.99 Canada Goose Men's Clothing Green 2001 Germany 2022-01-24 ORD-1351 Shipped Credit/Debit Card Green Parka 2 Standard Size L Outerwear 699.99 1399.98 Mango Women's Clothing Pink/White 2360 South Africa 2022-01-25 ORD-665 Delivered Credit/Debit Card Floral Midi Dress 2 Standard Size 6 Dresses 148.0 296.0 H&M Kids Kids Clothing Orange 2128 Canada 2022-01-26 ORD-428 Cancelled PayPal Orange Cargo Shorts 5 Standard Size 8 Shorts 22.99 114.94999999999999 Gap Men's Clothing Navy 2406 Egypt 2022-01-26 ORD-760 Shipped Cash on Delivery Classic Cotton T-Shirt 7 Express Size L Tops 24.99 174.92999999999998 Zara Men's Clothing Green 2365 Mexico 2022-01-26 ORD-384 Cancelled PayPal Green Utility Jacket 7 Standard Size XL Jackets 129.99 909.9300000000001 H&M Kids Kids Clothing Gray 2027 Italy 2022-01-27 ORD-567 Shipped Credit/Debit Card Gray Sweatshirt 5 Standard Size 6 Tops 19.99 99.94999999999999 J.Crew Men's Clothing Green 2092 United Kingdom 2022-01-27 ORD-1590 Delivered Credit/Debit Card Green Cargo Pants 1 Standard Size 32x32 Pants 89.99 89.99 J.Crew Women's Clothing Grey 2127 Netherlands 2022-01-28 ORD-1163 Shipped Credit/Debit Card Grey Knit Sweater 2 Standard Size L Sweaters 89.99 179.98 Brooks Brothers Men's Shoes Brown 2271 Greece 2022-01-29 ORD-641 Delivered Credit/Debit Card Brown Leather Loafers 3 Standard Size 10 Loafers 199.99 599.97 Mango Men's Clothing Red/Blue 2101 Norway 2022-01-29 ORD-1332 Delivered Credit/Debit Card Checkered Button-Down Shirt 2 Standard Size L Tops 49.99 99.98 Nike Kids Kids Clothing Purple 2253 Spain 2022-01-29 ORD-145 Delivered Credit/Debit Card Purple Leggings 8 Standard Size 7 Bottoms 16.99 135.92 Gap Kids Kids Clothing Yellow 2371 China 2022-01-30 ORD-165 Delivered Credit/Debit Card Yellow Graphic T-Shirt 3 Standard Size XS Tops 14.99 44.97 Brooks Brothers Men's Clothing Blue 2051 Brazil 2022-01-30 ORD-1219 Shipped Cash on Delivery Blue Dress Shirt 3 Express Size L Dress Shirts 89.99 269.96999999999997 Madewell Women's Clothing Black 2026 India 2022-01-30 ORD-108 Delivered Credit/Debit Card High-Rise Skinny Jeans 6 Standard Size 28 Jeans 128.0 768.0 Levi's Women's Clothing Black 2051 Netherlands 2022-01-30 ORD-1307 Delivered Credit/Debit Card Black Skinny Jeans 2 Standard Size 28 Jeans 69.99 139.98 Nike Men's Clothing Red 2350 Saudi Arabia 2022-01-31 ORD-964 Delivered Credit/Debit Card Men's Hooded Windbreaker 1 Standard Size M Jackets 79.99 79.99 Coach Accessories Black 2168 Switzerland 2022-02-01 ORD-118 Delivered Credit/Debit Card Leather Wallet 3 Standard One Size Wallets 250.0 750.0 J.Crew Men's Clothing Grey 2005 Saudi Arabia 2022-02-01 ORD-1057 Shipped Credit/Debit Card V-Neck Cashmere Sweater 2 Standard Size XL Sweaters 119.99 239.98 H&M Kids Kids Clothing Pink and Green 2262 Egypt 2022-02-01 ORD-721 Shipped Cash on Delivery Pink Floral Dress 8 Express Size 6 Dresses 24.99 199.92 Levi's Women's Clothing Dark Blue 1998 United Arab Emirates 2022-02-02 ORD-1327 Delivered Credit/Debit Card High-Waisted Skinny Jeans 2 Standard Size 28 Bottoms 79.99 159.98 Nike Kids Kids Clothing Black 2155 Spain 2022-02-02 ORD-452 Cancelled Credit/Debit Card Black Track Pants 3 Standard Size 10 Bottoms 29.99 89.97 Mango Women's Clothing Pink 2057 Hong Kong 2022-02-02 ORD-1585 Delivered Credit/Debit Card Pink Silk Blouse 2 Standard Size XS Tops 199.99 399.98 AllSaints Men's Clothing Black 2091 Tunisia 

### e. Create Delta Table ORDERS_GOLD

In [0]:
# Make sure you are using SupplyChainDB
spark.sql(f"USE SupplyChainDB")

## Create DeltaTable Orders_GOLD: 

ORDERS_Gold_df.write.mode("overwrite").format("delta").saveAsTable("ORDERS_Gold")

## Validate that the table was created successfully
display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

In [0]:
display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

-- Read more about different write options and parameters here https://docs.delta.io/latest/delta-batch.html#write-to-a-table 

* **Append** to automatically add new data to an existing Delta table, 
* **Overwrite** To automatically replace all the data in a table:

In [0]:
%sql
select * from ORDERS_Gold limit 5

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE TOTAL_ORDER H&M Kids Kids Clothing Pink and Green 2066 Hong Kong 2022-01-21 ORD-1281 Processing Credit/Debit Card Pink Floral Dress 3 Standard Size 6 Dresses 24.99 74.97 H&M Women's Clothing Cream 2254 Spain 2022-01-23 ORD-541 Delivered Credit/Debit Card Women's Faux Fur Coat 4 Standard Size M Outerwear 129.99 519.96 Canada Goose Men's Clothing Dark Green 2033 Hong Kong 2022-01-23 ORD-1388 Shipped Credit/Debit Card Men's Parka 2 Standard Size XL Jackets 999.99 1999.98 Zara Kids Kids Clothing Grey 2144 Switzerland 2022-01-24 ORD-1158 Delivered Credit/Debit Card Grey Hoodie 1 Standard Size L Sweatshirts 39.99 39.99 Canada Goose Men's Clothing Green 2001 Germany 2022-01-24 ORD-1351 Shipped Credit/Debit Card Green Parka 2 Standard Size L Outerwear 699.99 1399.98

Databricks data profile. Run in Databricks to view.

# TASK 5 - Query Orders Delta table using SQL

### Get Familiar with Orders_Gold dataset

In [0]:
%sql
-- Get top 30 rows Get Familiar with the Data
select * from supplychaindb.ORDERS_GOLD limit 30

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE TOTAL_ORDER H&M Kids Kids Clothing Pink and Green 2066 Hong Kong 2022-01-21 ORD-1281 Processing Credit/Debit Card Pink Floral Dress 3 Standard Size 6 Dresses 24.99 74.97 H&M Women's Clothing Cream 2254 Spain 2022-01-23 ORD-541 Delivered Credit/Debit Card Women's Faux Fur Coat 4 Standard Size M Outerwear 129.99 519.96 Canada Goose Men's Clothing Dark Green 2033 Hong Kong 2022-01-23 ORD-1388 Shipped Credit/Debit Card Men's Parka 2 Standard Size XL Jackets 999.99 1999.98 Zara Kids Kids Clothing Grey 2144 Switzerland 2022-01-24 ORD-1158 Delivered Credit/Debit Card Grey Hoodie 1 Standard Size L Sweatshirts 39.99 39.99 Canada Goose Men's Clothing Green 2001 Germany 2022-01-24 ORD-1351 Shipped Credit/Debit Card Green Parka 2 Standard Size L Outerwear 699.99 1399.98 Mango Women's Clothing Pink/White 2360 South Africa 2022-01-25 ORD-665 Delivered Credit/Debit Card Floral Midi Dress 2 Standard Size 6 Dresses 148.0 296.0 H&M Kids Kids Clothing Orange 2128 Canada 2022-01-26 ORD-428 Cancelled PayPal Orange Cargo Shorts 5 Standard Size 8 Shorts 22.99 114.94999999999999 Gap Men's Clothing Navy 2406 Egypt 2022-01-26 ORD-760 Shipped Cash on Delivery Classic Cotton T-Shirt 7 Express Size L Tops 24.99 174.92999999999998 Zara Men's Clothing Green 2365 Mexico 2022-01-26 ORD-384 Cancelled PayPal Green Utility Jacket 7 Standard Size XL Jackets 129.99 909.9300000000001 H&M Kids Kids Clothing Gray 2027 Italy 2022-01-27 ORD-567 Shipped Credit/Debit Card Gray Sweatshirt 5 Standard Size 6 Tops 19.99 99.94999999999999 J.Crew Men's Clothing Green 2092 United Kingdom 2022-01-27 ORD-1590 Delivered Credit/Debit Card Green Cargo Pants 1 Standard Size 32x32 Pants 89.99 89.99 Mango Women's Clothing Black 2023 Saudi Arabia 2022-01-28 ORD-829 Processing Credit/Debit Card Women's Leather Moto Jacket 3 Standard Size S Jackets 199.99 599.97 J.Crew Women's Clothing Grey 2127 Netherlands 2022-01-28 ORD-1163 Shipped Credit/Debit Card Grey Knit Sweater 2 Standard Size L Sweaters 89.99 179.98 Madewell Women's Clothing Blue 2041 Saudi Arabia 2022-01-28 ORD-193 Shipped Cash on Delivery Blue Denim Jacket 1 Standard Size M Jackets 99.99 99.99 Brooks Brothers Men's Shoes Brown 2271 Greece 2022-01-29 ORD-641 Delivered Credit/Debit Card Brown Leather Loafers 3 Standard Size 10 Loafers 199.99 599.97 Mango Men's Clothing Red/Blue 2101 Norway 2022-01-29 ORD-1332 Delivered Credit/Debit Card Checkered Button-Down Shirt 2 Standard Size L Tops 49.99 99.98 Nike Kids Kids Clothing Purple 2253 Spain 2022-01-29 ORD-145 Delivered Credit/Debit Card Purple Leggings 8 Standard Size 7 Bottoms 16.99 135.92 Gap Kids Kids Clothing Yellow 2371 China 2022-01-30 ORD-165 Delivered Credit/Debit Card Yellow Graphic T-Shirt 3 Standard Size XS Tops 14.99 44.97 Brooks Brothers Men's Clothing Blue 2051 Brazil 2022-01-30 ORD-1219 Shipped Cash on Delivery Blue Dress Shirt 3 Express Size L Dress Shirts 89.99 269.96999999999997 Madewell Women's Clothing Black 2026 India 2022-01-30 ORD-108 Delivered Credit/Debit Card High-Rise Skinny Jeans 6 Standard Size 28 Jeans 128.0 768.0 Levi's Women's Clothing Black 2051 Netherlands 2022-01-30 ORD-1307 Delivered Credit/Debit Card Black Skinny Jeans 2 Standard Size 28 Jeans 69.99 139.98 Nike Men's Clothing Red 2350 Saudi Arabia 2022-01-31 ORD-964 Delivered Credit/Debit Card Men's Hooded Windbreaker 1 Standard Size M Jackets 79.99 79.99 Coach Accessories Black 2168 Switzerland 2022-02-01 ORD-118 Delivered Credit/Debit Card Leather Wallet 3 Standard One Size Wallets 250.0 750.0 J.Crew Men's Clothing Grey 2005 Saudi Arabia 2022-02-01 ORD-1057 Shipped Credit/Debit Card V-Neck Cashmere Sweater 2 Standard Size XL Sweaters 119.99 239.98 H&M Kids Kids Clothing Pink and Green 2262 Egypt 2022-02-01 ORD-721 Shipped Cash on Delivery Pink Floral Dress 8 Express Size 6 Dresses 24.99 199.92 Levi's Women's Clothing Dark Blue 1998 

### KPI-1: Quantity Sold by Country

In [0]:
%sql
-- Dont forget to Filter out Cancelled Orders
select ORDER_COUNTRY, sum(QUANTITY) as TOTAL_DEMAND 
from supplychaindb.ORDERS_GOLD 
where ORDER_STATUS != "Cancelled" 
group by ORDER_COUNTRY 
sort by TOTAL_DEMAND desc

ORDER_COUNTRY TOTAL_DEMAND Germany 278 Switzerland 263 Saudi Arabia 254 Brazil 253 Greece 252 Canada 252 Tunisia 251 Norway 244 France 243 Netherlands 236 Japan 230 India 229 Portugal 227 United Arab Emirates 225 Mexico 217 United States 215 Spain 213 China 211 South Africa 192 Hong Kong 188 Denmark 185 Italy 181 Morocco 175 United Kingdom 170 Egypt 145

Databricks visualization. Run in Databricks to view.

### KPI-2: Sales by Division ($)

In [0]:
%sql
-- Division = CATEGORY 
-- Dont forget to Filter out Cancelled Orders
select CATEGORY, sum(TOTAL_ORDER) as Revenue
from supplychaindb.ORDERS_GOLD 
where ORDER_STATUS != "Cancelled" 
group by CATEGORY 
order by Revenue desc

CATEGORY Revenue Men's Clothing 403902.19000000006 Women's Clothing 275863.92000000004 Accessories 99434.47000000002 Kids Clothing 85677.17999999996 Men's Shoes 50567.42 Men's Accessories 31758.91 Women's Accessories 21388.93 Women's Shoes 10349.130000000001 Unisex Accessories 6899.540000000001

Databricks visualization. Run in Databricks to view.

### KPI-3: Top-5 Popular Brands

In [0]:
%sql
-- Limit Result to 5 and Order Results and order by Sold Quanity
select BRAND, sum(QUANTITY) as TOTAL_SOLD_ITEMS
from supplychaindb.ORDERS_GOLD 
-- where ORDER_STATUS != "Cancelled" 
group by BRAND 
order by TOTAL_SOLD_ITEMS desc
limit 5

BRAND TOTAL_SOLD_ITEMS Mango 679 Coach 436 Zara 418 Nike Kids 381 H&M Kids 365

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select count(ORDER_ID), ORDER_STATUS
from supplychaindb.ORDERS_GOLD 
where ORDER_STATUS = "Cancelled" 
group by ORDER_STATUS


count(ORDER_ID) ORDER_STATUS 178 Cancelled

# TASK 6 - Create Dashboard

In [0]:
# Use Databricks UI
# 1- Turn results of Previous Queries into visualisations
# 2- Create Dashboard and add Visualisations

# Practice Activity 2 : Add Monthly Sales Trend to your Dashboard

### KPI-4: Monthly Sales Trend (In QTY)

** Instructions :**  
  # 1- Query Delta Table: Orders_Gold to extract Monthly Sales (in Quantity, across all brands and all regions) 
  # 2- Turn the result (Table) into a visualisation (line chart) to Show the Trend for the last 18 months.
  # 3- Add your visualization to the Supply Chain Dashboard.

In [0]:
%sql
-- Use DATE_TRUNC()  
select DATE_TRUNC('month',ORDER_DATE) as Month, sum(QUANTITY) as TOTAL_DEMAND 
from supplychaindb.ORDERS_GOLD 
where ORDER_STATUS != "Cancelled" 
group by 1
order by 1 asc

Month TOTAL_DEMAND 2022-01-01T00:00:00.000+0000 61 2022-02-01T00:00:00.000+0000 156 2022-03-01T00:00:00.000+0000 192 2022-04-01T00:00:00.000+0000 167 2022-05-01T00:00:00.000+0000 200 2022-06-01T00:00:00.000+0000 198 2022-07-01T00:00:00.000+0000 433 2022-08-01T00:00:00.000+0000 332 2022-09-01T00:00:00.000+0000 479 2022-10-01T00:00:00.000+0000 456 2022-11-01T00:00:00.000+0000 392 2022-12-01T00:00:00.000+0000 400 2023-01-01T00:00:00.000+0000 413 2023-02-01T00:00:00.000+0000 396 2023-03-01T00:00:00.000+0000 539 2023-04-01T00:00:00.000+0000 360 2023-05-01T00:00:00.000+0000 241 2023-06-01T00:00:00.000+0000 114

Databricks visualization. Run in Databricks to view.

# TASK 7 - Update Data in Orders table using Merge

<img src="https://databricks.com/wp-content/uploads/2020/09/delta-lake-medallion-model-scaled.jpg" width=1012/>

### a. Upload Json files into DBFS

Use UI to upload the file "UPDATE_ORDERS_RAW.json" into DBFS, use the same folder dbfs:/FileStore/SupplyChain/ORDERS_RAW/

### b. Read file using Spark dataframe

In [0]:
# Read multiple line json file UPDATE_ORDERS_RAW.json
Update_orders_df = spark.read.option("multiline", "true").json("dbfs:/FileStore/SupplyChain/ORDERS_RAW/UPDATE_ORDERS_RAW.json")

## Show the datafarme
display(Update_orders_df)

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE H&M Kids Kids Clothing Pink and Green 2066 Hong Kong 2022-01-21 ORD-1281 Delivered Credit/Debit Card Pink Floral Dress 4 Standard Size 6 Dresses 24.99 Mango Women's Clothing Black 2023 Saudi Arabia 2022-01-28 ORD-829 Delivered Credit/Debit Card Women's Leather Moto Jacket 3 Standard Size S Jackets 199.99 Madewell Women's Clothing Blue 2041 Saudi Arabia 2022-01-28 ORD-193 Delivered Cash on Delivery Blue Denim Jacket 3 Standard Size M Jackets 99.99 Barbour Men's Clothing Navy 2074 Norway 2022-05-29 ORD-826 Cancelled Credit/Debit Card Men's Quilted Jacket 0 Standard Size L Jackets 299.99 Gap Kids Kids Clothing Red 2393 Saudi Arabia 2022-05-30 ORD-842 Cancelled Credit/Debit Card Red Graphic T-shirt 0 Standard Size 8 Tops 14.99

-->Check the original data **BEFORE MERGE**

In [0]:
%sql 
select ORDER_ID,ORDER_STATUS,Quantity from Supplychaindb.ORDERS_RAW WHERE ORDER_ID in ("ORD-1281","ORD-829","ORD-193","ORD-826","ORD-842")

ORDER_ID ORDER_STATUS Quantity ORD-1281 Processing 3 ORD-829 Processing 3 ORD-193 Shipped 1 ORD-826 Processing 10 ORD-842 Processing 10

### c. Update Orders_RAW deltatable using Merge

In [0]:
%sql
DESCRIBE DETAIL supplychaindb.ORDERS_RAW

format id name description location createdAt lastModified partitionColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion tableFeatures statistics delta 23830470-b360-4716-a305-52e44d1767d4 spark_catalog.supplychaindb.orders_raw null dbfs:/user/hive/warehouse/supplychaindb.db/orders_raw 2024-01-02T09:18:04.454+0000 2024-01-05T16:16:22.000+0000 List() 4 57492 Map() 1 2 List(appendOnly, invariants) Map()

In [0]:
from delta.tables import *

# programmatically interacting with Delta tables using the class delta.tables.DeltaTable(spark: pyspark.sql.session.SparkSession, jdt: JavaObject)
delta_orders_raw =  DeltaTable.forPath(spark, "dbfs:/user/hive/warehouse/supplychaindb.db/orders_raw")

In [0]:
display(delta_orders_raw)

In [0]:
## merge data into delta Table ORDER_RAW
# DOCUMENTATION https://docs.delta.io/latest/delta-update.html#language-python 

delta_orders_raw.alias("ORDERS_RAW").merge(Update_orders_df.alias("UpdateOrders"), 
                                            "ORDERS_RAW.ORDER_ID = UpdateOrders.ORDER_ID")\
                                              .whenMatchedUpdateAll()\
                                                .whenNotMatchedInsertAll()\
                                                  .execute()

# must be at least one WHEN clause in a MERGE statement.

--> check the udaptes rows **AFTER MERGE**

In [0]:
%sql 
select ORDER_ID,ORDER_STATUS,Quantity from SUPPLYCHAINDB.ORDERS_RAW WHERE ORDER_ID in ("ORD-1281","ORD-829","ORD-193","ORD-826","ORD-842")

ORDER_ID ORDER_STATUS Quantity ORD-1281 Delivered 4 ORD-829 Delivered 3 ORD-193 Delivered 3 ORD-826 Cancelled 0 ORD-842 Cancelled 0

Learn More about Merge Operations check out https://docs.delta.io/latest/delta-update.html#language-python

# TASK 8 - Query previous versions of delta table using **Time Travel**

**This Task shows how to time travel between different versions of a Delta table with Delta Lake. You can time travel by table version or by timestamp. You’ll learn about the benefits of time travel and why it’s an essential feature for production data workloads.**

**Documentation : https://delta.io/blog/2023-02-01-delta-lake-time-travel/** 

<img src="https://delta.io/static/9c42ea9f028932de03257ed75d35a8ba/cf8e5/image1.png" width=1012/>

### a. Describe Detla Table History:

In [0]:
%sql
-- Check Table History 
describe history supplychaindb.orders_raw
-- Use the UI to see Delta Table History

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 9 2024-01-05T16:17:27.000+0000 6733151700230882 ciprianhancu@gmail.com MERGE Map(predicate -> ["(ORDER_ID#170737 = ORDER_ID#170471)"], matchedPredicates -> [{"actionType":"update"}], notMatchedPredicates -> [{"actionType":"insert"}], notMatchedBySourcePredicates -> []) null List(2356186753306815) 0105-135557-o6edkyku 8 WriteSerializable false Map(numTargetRowsCopied -> 495, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 2, numTargetBytesAdded -> 22755, numTargetBytesRemoved -> 17717, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 5, executionTimeMs -> 4758, numTargetRowsInserted -> 0, numTargetRowsMatchedDeleted -> 0, scanTimeMs -> 1840, numTargetRowsUpdated -> 5, numOutputRows -> 500, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 5, numTargetFilesRemoved -> 1, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 2547) null Databricks-Runtime/12.2.x-scala2.12 8 2024-01-05T16:16:22.000+0000 6733151700230882 ciprianhancu@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(isManaged -> true, description -> null, partitionBy -> [], properties -> {}) null List(2356186753306815) 0105-135557-o6edkyku 7 WriteSerializable false Map(numFiles -> 4, numOutputRows -> 1510, numOutputBytes -> 57492) null Databricks-Runtime/12.2.x-scala2.12 7 2024-01-05T14:04:56.000+0000 6733151700230882 ciprianhancu@gmail.com MERGE Map(predicate -> ["(ORDER_ID#6184 = ORDER_ID#5918)"], matchedPredicates -> [{"actionType":"update"}], notMatchedPredicates -> [{"actionType":"insert"}], notMatchedBySourcePredicates -> []) null List(2356186753306815) 0105-135557-o6edkyku 6 WriteSerializable false Map(numTargetRowsCopied -> 495, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 2, numTargetBytesAdded -> 22755, numTargetBytesRemoved -> 17717, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 5, executionTimeMs -> 9370, numTargetRowsInserted -> 0, numTargetRowsMatchedDeleted -> 0, scanTimeMs -> 4072, numTargetRowsUpdated -> 5, numOutputRows -> 500, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 5, numTargetFilesRemoved -> 1, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 4240) null Databricks-Runtime/12.2.x-scala2.12 6 2024-01-05T14:03:12.000+0000 6733151700230882 ciprianhancu@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(isManaged -> true, description -> null, partitionBy -> [], properties -> {}) null List(2356186753306815) 0105-135557-o6edkyku 5 WriteSerializable false Map(numFiles -> 4, numOutputRows -> 1510, numOutputBytes -> 57492) null Databricks-Runtime/12.2.x-scala2.12 5 2024-01-04T17:15:26.000+0000 6733151700230882 ciprianhancu@gmail.com MERGE Map(predicate -> ["(ORDER_ID#7144 = ORDER_ID#6858)"], matchedPredicates -> [{"actionType":"update"}], notMatchedPredicates -> [{"actionType":"insert"}], notMatchedBySourcePredicates -> []) null List(2356186753306815) 0104-153301-wshz37tj 4 WriteSerializable false Map(numTargetRowsCopied -> 495, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 2, numTargetBytesAdded -> 22755, numTargetBytesRemoved -> 17717, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 5, executionTimeMs -> 9603, numTargetRowsInserted -> 0, numTargetRowsMatchedDeleted -> 0, scanTimeMs -> 3817, numTargetRowsUpdated -> 5, numOutputRows -> 500, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 5, numTargetFilesRemoved -> 1, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 4141) null Databricks-Runtime/12.2.x-scala2.12 4 2024-01-04T15:36:37.000+0000 6733151700230882 ciprianhancu@gmail.com CREATE OR REPLACE TABLE AS SELECT Map(isManaged -> true, des

### b. Using SQL:

In [0]:
%sql 
 select ORDER_ID,ORDER_STATUS,Quantity 
 from SUPPLYCHAINDB.ORDERS_RAW VERSION AS OF 5 
 WHERE ORDER_ID in ("ORD-1281","ORD-829","ORD-193","ORD-826","ORD-842")

-- CHange Version Number to See different Versions of the delta table

ORDER_ID ORDER_STATUS Quantity ORD-1281 Delivered 4 ORD-829 Delivered 3 ORD-193 Delivered 3 ORD-826 Cancelled 0 ORD-842 Cancelled 0

### c. Using Spark dataframe:

In [0]:
#Time Travel
version_1 = spark.read.format('delta').option('TimeStamp', "2023-05-16").table("SUPPLYCHAINDB.ORDERS_RAW")
display(version_1)

BRAND CATEGORY COLOR CUSTOMER_ID ORDER_COUNTRY ORDER_DATE ORDER_ID ORDER_STATUS PAYMENT_METHOD PRODUCT_NAME QUANTITY SHIPPING_METHOD SIZE SUB-CATEGORY UNIT_PRICE H&M Women's Clothing Cream 2254 Spain 2022-01-23 ORD-541 Delivered Credit/Debit Card Women's Faux Fur Coat 4 Standard Size M Outerwear 129.99 Canada Goose Men's Clothing Dark Green 2033 Hong Kong 2022-01-23 ORD-1388 Shipped Credit/Debit Card Men's Parka 2 Standard Size XL Jackets 999.99 Zara Kids Kids Clothing Grey 2144 Switzerland 2022-01-24 ORD-1158 Delivered Credit/Debit Card Grey Hoodie 1 Standard Size L Sweatshirts 39.99 Canada Goose Men's Clothing Green 2001 Germany 2022-01-24 ORD-1351 Shipped Credit/Debit Card Green Parka 2 Standard Size L Outerwear 699.99 Mango Women's Clothing Pink/White 2360 South Africa 2022-01-25 ORD-665 Delivered Credit/Debit Card Floral Midi Dress 2 Standard Size 6 Dresses 148.0 H&M Kids Kids Clothing Orange 2128 Canada 2022-01-26 ORD-428 Cancelled PayPal Orange Cargo Shorts 5 Standard Size 8 Shorts 22.99 Gap Men's Clothing Navy 2406 Egypt 2022-01-26 ORD-760 Shipped Cash on Delivery Classic Cotton T-Shirt 7 Express Size L Tops 24.99 Zara Men's Clothing Green 2365 Mexico 2022-01-26 ORD-384 Cancelled PayPal Green Utility Jacket 7 Standard Size XL Jackets 129.99 H&M Kids Kids Clothing Gray 2027 Italy 2022-01-27 ORD-567 Shipped Credit/Debit Card Gray Sweatshirt 5 Standard Size 6 Tops 19.99 J.Crew Men's Clothing Green 2092 United Kingdom 2022-01-27 ORD-1590 Delivered Credit/Debit Card Green Cargo Pants 1 Standard Size 32x32 Pants 89.99 J.Crew Women's Clothing Grey 2127 Netherlands 2022-01-28 ORD-1163 Shipped Credit/Debit Card Grey Knit Sweater 2 Standard Size L Sweaters 89.99 Brooks Brothers Men's Shoes Brown 2271 Greece 2022-01-29 ORD-641 Delivered Credit/Debit Card Brown Leather Loafers 3 Standard Size 10 Loafers 199.99 Mango Men's Clothing Red/Blue 2101 Norway 2022-01-29 ORD-1332 Delivered Credit/Debit Card Checkered Button-Down Shirt 2 Standard Size L Tops 49.99 Nike Kids Kids Clothing Purple 2253 Spain 2022-01-29 ORD-145 Delivered Credit/Debit Card Purple Leggings 8 Standard Size 7 Bottoms 16.99 Gap Kids Kids Clothing Yellow 2371 China 2022-01-30 ORD-165 Delivered Credit/Debit Card Yellow Graphic T-Shirt 3 Standard Size XS Tops 14.99 Brooks Brothers Men's Clothing Blue 2051 Brazil 2022-01-30 ORD-1219 Shipped Cash on Delivery Blue Dress Shirt 3 Express Size L Dress Shirts 89.99 Madewell Women's Clothing Black 2026 India 2022-01-30 ORD-108 Delivered Credit/Debit Card High-Rise Skinny Jeans 6 Standard Size 28 Jeans 128.0 Levi's Women's Clothing Black 2051 Netherlands 2022-01-30 ORD-1307 Delivered Credit/Debit Card Black Skinny Jeans 2 Standard Size 28 Jeans 69.99 Nike Men's Clothing Red 2350 Saudi Arabia 2022-01-31 ORD-964 Delivered Credit/Debit Card Men's Hooded Windbreaker 1 Standard Size M Jackets 79.99 Coach Accessories Black 2168 Switzerland 2022-02-01 ORD-118 Delivered Credit/Debit Card Leather Wallet 3 Standard One Size Wallets 250.0 J.Crew Men's Clothing Grey 2005 Saudi Arabia 2022-02-01 ORD-1057 Shipped Credit/Debit Card V-Neck Cashmere Sweater 2 Standard Size XL Sweaters 119.99 H&M Kids Kids Clothing Pink and Green 2262 Egypt 2022-02-01 ORD-721 Shipped Cash on Delivery Pink Floral Dress 8 Express Size 6 Dresses 24.99 Levi's Women's Clothing Dark Blue 1998 United Arab Emirates 2022-02-02 ORD-1327 Delivered Credit/Debit Card High-Waisted Skinny Jeans 2 Standard Size 28 Bottoms 79.99 Nike Kids Kids Clothing Black 2155 Spain 2022-02-02 ORD-452 Cancelled Credit/Debit Card Black Track Pants 3 Standard Size 10 Bottoms 29.99 Mango Women's Clothing Pink 2057 Hong Kong 2022-02-02 ORD-1585 Delivered Credit/Debit Card Pink Silk Blouse 2 Standard Size XS Tops 199.99 AllSaints Men's Clothing Black 2091 Tunisia 2022-02-02 ORD-1209 Shipped Cash on Delivery Black Leather Jacket 1 Express Size M Jackets 499.99 Banana Republic Men's Clothing White 2071 Hong Kong 2022-02-02 ORD-1161 Shipped Credit/Debit Card White Button-up Shirt 2 Standard Size L Sh

# END OF THE PROJECT

# CUMULATIVE CHALLENGE

**Your Task :</br> Using the “Inventory” data, your task is to enrich the Supply Chain Dashboard with the list of low-stock and out-of-stock Items.** 

Using Databricks notebook you will : </br>
1-Upload INVENTORY.JSON file to DBFS(1) </br>
2-Read the file using spark dataframe (1)</br>
3-Create Delta Table INVENTORY (1)</br>
4-Write an SQL query to cross join ORDERS_GOLD and INVENTORY DeltaTables to find the list of Items Low-in Stock or Out-of Stock</br>
5-Turn the result into a Visualisation (Table type) and Add it to your SupplyChain Dashboard</br>

</br>(1) Skip if you have completed Practice Activity 1

### a. Upload INVENTORY.Json file in DBFS

In [0]:
## Load the file using the UI to this path dbfs:/FileStore/SupplyChain/INVENTORY/

### b. Read the File using spark dataframe

In [0]:
# inventory_df =

## Show the datafarme
inventory_df.show(n=5, truncate=False)

+-------+----------+--------------------------+----------+-----+
|BRAND  |COLOR     |PRODUCT_NAME              |SIZE      |STOCK|
+-------+----------+--------------------------+----------+-----+
|J.Crew |Green     |Green Cargo Pants         |Size 32x32|58   |
|Theory |Grey      |Grey Turtleneck Sweater   |Size S    |42   |
|Ray-Ban|Gold/Brown|Classic Aviator Sunglasses|One Size  |53   |
|ASOS   |Black     |Men's Faux Leather Jacket |Size M    |40   |
|Levi's |Light Blue|Distressed Denim Shorts   |Size M    |46   |
+-------+----------+--------------------------+----------+-----+
only showing top 5 rows



### c. Create Delta Table INVENTORY <img src="https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png" width=35 height=35/>

In [0]:
# Use SupplyChainDB Database
db = "SupplyChainDB"
spark.sql(f"USE {db}")

Out[121]: DataFrame[]

In [0]:
## Create INVENTORY Delta Table 
# inventory_df. 

## Validate that the table was created successfully
display(spark.sql(f"SHOW TABLES"))

database tableName isTemporary supplychaindb inventory false supplychaindb orders_gold false supplychaindb orders_raw false

### d. Cross Join ORDERS_GOLD and INVENTORY DeltaTables to find the list of Low Stock or Out-of Stock Items

**Your Goal** is to find the list of Low-Stock or Out-of-Stock Items and Add the result to your SupplyChain Dashboard<br />
**Hints:**
* Group all Orders (from ORDERS_GOLD) based-on BRAND, COLOR, PRODUCT_NAME AND SIZE And Add QTY_SOLD (SUM QUANTITY) 
* Cross join the result with INVENTORY using an inner join on BRAND, PRODUCT_NAME, COLOR AND SIZE.
* Add calculated column "QTY_LEFT_STOCK" as (STOCK - QTY_SOLD)
* Filter-out Cancelled ORDERS (ORDER_STATUS)
* Keep only Items with QTY_LEFT_STOCK < 20
* Sort the result by "QTY_LEFT_STOCK" in ascending order

In [0]:
%sql

select * FROM (
select O.BRAND, O.COLOR, O.PRODUCT_NAME, O.SIZE, I.STOCK, sum(O.QUANTITY) as QTY_SOLD, (I.STOCK - QTY_SOLD) AS QTY_LEFT_STOCK
from supplychaindb.ORDERS_GOLD O
inner join supplychaindb.INVENTORY I
ON O.BRAND=I.BRAND AND O.COLOR=I.COLOR AND O.PRODUCT_NAME=I.PRODUCT_NAME AND O.SIZE=I.SIZE
where O.ORDER_STATUS != "Cancelled" 
group by O.BRAND, O.COLOR, O.PRODUCT_NAME, O.SIZE, I.STOCK
)
where QTY_LEFT_STOCK < 20
order by QTY_LEFT_STOCK

BRAND COLOR PRODUCT_NAME SIZE STOCK QTY_SOLD QTY_LEFT_STOCK ASOS Black Men's Faux Leather Jacket Size M 40 37 3 Gap Navy Classic Cotton T-Shirt Size L 44 40 4 Theory Grey Grey Turtleneck Sweater Size S 42 37 5 J.Crew Green Green Cargo Pants Size 32x32 58 52 6 Ray-Ban Gold/Brown Classic Aviator Sunglasses One Size 53 46 7 Levi's Light Blue Distressed Denim Shorts Size M 46 36 10 Steve Madden Black Lace-Up Combat Boots Size 8 65 55 10 Coach Black Leather Crossbody Bag One Size 53 40 13 Nike Kids Gray Gray Joggers Size 12 50 36 14 Dr. Martens Black Black Leather Chelsea Boots Size 10 61 45 16 H&M Kids Green Green Camo Pants Size 5 59 42 17 Zara Kids Red and Black Red Plaid Button-Up Shirt Size 4 59 42 17 Allen Edmonds Brown Brown Leather Belt Size 34 55 37 18 Zara Olive Green Men's Bomber Jacket Size L 62 44 18 H&M Kids Orange Orange Cargo Shorts Size 8 44 26 18 Gap Kids Pink Pink Floral Dress Size 6 63 44 19

Databricks visualization. Run in Databricks to view.

### e. Turn the result into a Visualisation (Table) and Add it to SupplyChain Dashboard

In [0]:
# Use Databricks UI to Turn results into a visualisation and then add it to your SupplyChain Dashboard

#  
   <img src="https://www.freeiconspng.com/uploads/congratulations-png-1.png" width=350/>
   .... THIS IS THE END OF THE GUIDED PROJECT